In [1]:
from tensorflow.keras import callbacks, optimizers
import sys
sys.path.append("../..")
from Shared.Data.yolov4_210.py_src.yolov4.tf import SaveWeightsCallback, YOLOv4
import time
import datetime

start = datetime.datetime.now()
print( start )

yolo = YOLOv4(tiny=True)
yolo.classes = "/nfs/Shared/Data/coco.names"
yolo.input_size = 608
yolo.batch_size = 32

yolo.make_model(activation1="relu")
yolo.load_weights(
    "/nfs/Shared/Data/yolov4-tiny.conv.29_AlexeyAB",
    weights_type="yolo"
)

train_data_set = yolo.load_dataset(
    "/nfs/Shared/Data/train2017.txt",
    image_path_prefix="/nfs/Shared/Data/train2017",
    label_smoothing=0.05
)
val_data_set = yolo.load_dataset(
    "/nfs/Shared/Data/val2017.txt",
    image_path_prefix="/nfs/Shared/Data/val2017",
    training=False
)

epochs = 400
lr = 1e-4

optimizer = optimizers.Adam(learning_rate=lr)
yolo.compile(optimizer=optimizer, loss_iou_type="ciou")

def lr_scheduler(epoch):
    if epoch < int(epochs * 0.5):
        return lr
    if epoch < int(epochs * 0.8):
        return lr * 0.5
    if epoch < int(epochs * 0.9):
        return lr * 0.1
    return lr * 0.01

_callbacks = [
    callbacks.LearningRateScheduler(lr_scheduler),
    callbacks.TerminateOnNaN(),
    callbacks.TensorBoard(
        log_dir="logs",
    ),
    SaveWeightsCallback(
        yolo=yolo, dir_path="trained",
        weights_type="yolo", epoch_per_save=10
    ),
]

yolo.fit(
    train_data_set,
    epochs=epochs,
    callbacks=_callbacks,
    validation_data=val_data_set,
    validation_steps=50,
    validation_freq=5,
    steps_per_epoch=100,
)

end = datetime.datetime.now()
print("start:" ,start)
print("end:" ,end)
print("total:" ,end - start)

Call tf.config.experimental.set_memory_growth(GPU0, True)
2021-03-12 16:15:22.102217
Epoch 1/400
grid: 38*38 iou_loss: 24.5659447 conf_loss: 3046.41748 prob_loss: 393.625977 total_loss 3464.60938
grid: 19*19 iou_loss: 20.6828079 conf_loss: 696.935791 prob_loss: 372.490784 total_loss 1090.10938
grid: 38*38 iou_loss: 37.0042877 conf_loss: 3012.24414 prob_loss: 570.891052 total_loss 3620.13965
grid: 19*19 iou_loss: 17.7273502 conf_loss: 682.262451 prob_loss: 316.877472 total_loss 1016.86725
grid: 38*38 iou_loss: 26.7768974 conf_loss: 2976.24707 prob_loss: 407.235016 total_loss 3410.25903
grid: 19*19 iou_loss: 14.474021 conf_loss: 668.140747 prob_loss: 261.002502 total_loss 943.617249
grid: 38*38 iou_loss: 35.671051 conf_loss: 2946.09814 prob_loss: 528.458923 total_loss 3510.22827
grid: 19*19 iou_loss: 19.8507748 conf_loss: 658.368774 prob_loss: 342.90979 total_loss 1021.12933
grid: 38*38 iou_loss: 29.2900467 conf_loss: 2907.89917 prob_loss: 474.457336 total_loss 3411.64648
grid: 19*19 iou

In [13]:
import sys
sys.path.append("../..")
from Shared.Data.yolov4_210.py_src.yolov4.tf import YOLOv4

yolo = YOLOv4(tiny=True, tpu=True)

yolo.classes = "/nfs/Shared/Data/coco.names"
yolo.input_size = (512, 384) # width, height
yolo.make_model(activation1="relu")

yolo.load_weights("trained/yolov4-tiny-310.weights", weights_type="yolo")

dataset = yolo.load_dataset(
    "/nfs/Shared/Data/train2017.txt",
    training=False,
    image_path_prefix="/nfs/Shared/Data/train2017"
)

yolo.save_as_tflite(
    "convert_model/yolov4-tiny-310-relu-int8.tflite",
    quantization="full_int8",
    data_set=dataset,
    num_calibration_steps=400
)

INFO:tensorflow:Assets written to: /tmp/tmp7ybag216/assets


INFO:tensorflow:Assets written to: /tmp/tmp7ybag216/assets


In [14]:
!edgetpu_compiler -sa convert_model/yolov4-tiny-310-relu-int8.tflite -o convert_model

Edge TPU Compiler version 15.0.340273435

Model compiled successfully in 1462 ms.

Input model: convert_model/yolov4-tiny-310-relu-int8.tflite
Input size: 5.94MiB
Output model: convert_model/yolov4-tiny-310-relu-int8_edgetpu.tflite
Output size: 6.33MiB
On-chip memory used for caching model parameters: 6.06MiB
On-chip memory remaining for caching model parameters: 1.66MiB
Off-chip memory used for streaming uncached model parameters: 3.38KiB
Number of Edge TPU subgraphs: 3
Total number of operations: 132
Operation log: convert_model/yolov4-tiny-310-relu-int8_edgetpu.log

Model successfully compiled but not all operations are supported by the Edge TPU. A percentage of the model will instead run on the CPU, which is slower. If possible, consider updating your model to use only operations supported by the Edge TPU. For details, visit g.co/coral/model-reqs.
Number of operations that will run on Edge TPU: 101
Number of operations that will run on CPU: 31

Operator                       Count 

In [1]:
import sys
sys.path.append("../..")
from yolov4_210.yolov4_210.py_src.yolov4.tflite import YOLOv4
import cv2

yolo = YOLOv4(tiny=True, tpu=True)

yolo.classes = "C:/Users/CSS-WU/Documents/GitHub/Machine_Learning/YoloV4/hhk7734/coco.names"

yolo.load_tflite("convert_model/yolov4-tiny-160-relu-int8_edgetpu.tflite")

yolo.inference(
    "C:/Users/CSS-WU/Desktop/cam6.mp4",
    is_image=False,
    cv_apiPreference=cv2.CAP_ANY,
    # cv_waitKey_delay= 25,
    cv_frame_size=(1920, 1080),
    cv_fourcc="YUYV",
)

YOLOv4: Inference is finished
